# GeoStacks: a library for efficient query and stacking of satellite remote sensing data sets

## Author(s)

- Author1 = {"name": "Shane Grigsby",     "affiliation": "University of Maryland / NASA Goddard Center", "email": "grigsby@umd.edu",              "orcid": "0000-0003-4904-7785"}
- Author2 = {"name": "Whyjay Zheng",      "affiliation": "University of California Berkeley",            "email": "whyjz@berkeley.edu",           "orcid": "0000-0002-2316-2614"}
- Author3 = {"name": "Jonathan Taylor",   "affiliation": "Stanford University",                          "email": "jonathan.taylor@stanford.edu", "orcid": "0000-0002-1716-7160"}
- Author4 = {"name": "Facundo Sapienza",  "affiliation": "University of California Berkeley",            "email": "fsapienza@berkeley.edu",       "orcid": "0000-0003-4252-7161"}
- Author5 = {"name": "Tasha Snow",        "affiliation": "Colorado School of Mines",                     "email": "tsnow@mines.edu",              "orcid": "0000-0001-5697-5470"}
- Author6 = {"name": "Fernando Pérez",    "affiliation": "University of California Berkeley",            "email": "fernando.perez@berkeley.edu",  "orcid": "0000-0002-1725-9815"}
- Author7 = {"name": "Matthew Siegfried", "affiliation": "Colorado School of Mines",                     "email": "siegfried@mines.edu",          "orcid": "0000-0002-0868-4633"}

## Purpose
This notebook demonstrates two related tasks for Earth Science investigations using remote sensing data:

 1. Data Discovery
 2. Scriptable and reproducible data retrieval
 
These tasks are broadly the ‘data ingest’ portion of Earth science research. Although reproducible science tends to focus on publicly available code that produces consistent and traceable outputs, most data ingest tasks (e.g., downloading a subset of Landsat or MODIS files) are manual. This breaks the chain of reproducibility: a collaborator or other investigator may not use the same input files from the same data collection. Further, downloading these datasets adds substantial overhead to validating or expanding analysis.

In this notebook, we demonstrate a method of data retrieval that is scriptable, so that an analysis notebook can contain both the analytic code and calls to manifest the input data, in a consistent and reproducible way.

## Technical contributions

We demonstrate a simple use case using Landsat 8 data---pulling a time series of data for a location and calculating estimated cloud cover over the area. Although the Landsat-8 (Collection 1) data we use is considered a Level 3 Gridded data product, the process would be similar for Level 3 MODIS data and can be adapted for similar retrieval of Level 2 swath data products. The process shown includes an interactive data discovery stage (i.e. determining the scene(s) of interest). If the study area is already known, these first steps can be omitted and the retrieval code can be used alone.

Part of reproducible and open science is reducing barriers to adoption. Some of the techniques that we show do have mature analogues that already exist in the community. We use Landsat data in this demonstration, and a clear question is: why not use the USGS and NASA data discovery tools? These online viewers facilitate data discovery and download; it is also possible to use file lists and/or generated download scripts to recreate dataset directories in an automated way. So why this library? Several reasons motivate development:

 - LandLook and similar interactive viewers are not scriptable for data download
 - EarthData portals can produce download scripts, but require login credentials that sometimes differ from your EarthData login
 - All of the existing retrieval methods are multi-step:
   - File lists must be parsed and pointed to data source repositories
   - Auto-generated scripts must be configured with credentials
   - Retrievals are only to disk and not to memory, requiring further scripting
 - None of the existing methods pull data in a way conducive to a cloud workflow

We weave several modern projects together for a cohesive remote sensing data retrieval workflow. Specifically, we use the following libraries:

 - Intake for catalog templating and semantic dataset access
 - Xarray and Dask for distributed representation of data rasters (via Intake-xarray)
 - ipyleaflet for display of scene footprints and data exploration
 - Pandas for metadata access and management
 - sklearn for fast spatial indexing in spherical coordinates
 - GeoStacks, our library to glue everything together


## Methodology

Landsat 8 data is stored on the fixed World Reference System 2 (WRS-2) grid, which uses path and row coordinates to map and grid data acquisitions. We use a multi-year catalog of corrected scene center and corner locations to index available data scenes. After providing a query lat/lon point, a two-tier search process is conducted: first using haversine distances to prune the tree in an approximate manner, then with point in polygon checks to refine the data search. This search process accomplishes several objectives:

 - Finds all relevant scenes. Scene overlap increases towards the poles, and a single data site may have more data acquisitions in the polar regions.
 - Removes false positives by ensuring that selected scenes have actual data of interest. This is important because the metadata of the raster files describe the bounds of the data grid, but the bearing of the flight path causes large no-data areas in the corners of the data grids when the image is projected onto the Earth surface. We use the acquisition footprints to only select granules that have valid data at the query point.
 - Find only valid scenes. Landsat does not acquire data at all path/row combinations; some of the path/row combinations are over ocean, or occur at nighttime hours that there is no data telemetered for that path/row.

Data can be selected for either single time steps, or time ranges.


## Results

We demonstrate a flexible, yet reproducible, user-friendly cloud-based remote sensing data query, fetch, and analysis workflow using the nascent ‘GeoStacks’ library to retrieve Landsat scenes in the Arctic. We calculate a simple statistic (i.e., total cloud cover) for our fetched data, to demonstrate that any data analysis or processing tasks can be added for an end-to-end workflow. A one-stop-shop for the earth science data analytics of the future. 

## Funding
Include references to awards that supported this research. Add as many award references as you need.

- Award1 = {"agency": "US National Science Foundation", "award_code": "1928406", "award_URL": "https://nsf.gov/awardsearch/showAward?AWD_ID=1928406 " }
- Award2 = {"agency": "US National Science Foundation", "award_code": "1928374", "award_URL": "https://nsf.gov/awardsearch/showAward?AWD_ID=1928374 " }
- Award3 = {"agency": "NASA", "award_code": "80NSSC20K1878", "award_URL": "https://www.nasa.gov/centers/nssc/forms/grant-status-form/ "}

## Keywords

keywords=[“Cloud-computing”, “Remote Sensing”, “Landsat 8”, “Jupyter notebook”, “Data Ingest”]

## Citation


Grisby, S., Zheng, W., Taylor, J.,  Sapienza, F., Snow, T., Pérez, F., & Siegfried, M. (2021). GeoStacks: a library for efficient query and stacking of satellite remote sensing data sets. Accessed x/x/xxxx at https://github.com/geostacks/GeoStacks


## Work In Progress - improvements

Notable TODOs:

- [ ] Improve plotting of cloud data for easier interpretation
- [ ] Add additional comments and text in cells for explanation 
- [ ] Add additional hyperlinks to resources 

## Suggested next steps

Work on the GeoStacks library is at an early stage and is ongoing. We look forward to implementing additional improvements in the near future:

 - More data source catalogs
 - Convenience functions for merging overlapping rasters
 - Associated cross data search (what other remote sensing data is coincident with this scene?)

Pull requests and feedback are welcome and appreciated!


## Acknowledgements 
Include any relevant acknowledgements, apart from funding (which was in section 1.6)

In [1]:
# Autoreload extension
%load_ext autoreload
%autoreload 2

%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [2]:
cd ../..

/home/espg/software/blanktest/GeoStacks


In [3]:
# Load geostacks
from geostacks import SpatialIndexLS8, GeoStacksUI

# Load date parsing
from datetime import datetime
import pandas as pd

# Array support
import xarray as xr

# Load dask, suppress warnings
from dask.distributed import Client
import logging

## Spatial Index Object

The base spatial indexing object combines several features of the sensor data catalog. It includes the footprint database of all valid Landsat 8 path/row combinations:

In [4]:
ls8 = SpatialIndexLS8()
ls8.data

path  row    lat_CTR    lon_CTR     lat_UL     lon_UL     lat_UR  \
0         1    2  80.002493  -4.197763  81.205697  -2.730017  79.717460   
1         1    3  79.111023 -10.561457  80.332344  -9.994770  78.957946   
2         1    4  78.118527 -15.970556  79.344246 -16.045440  78.079664   
3         1    5  77.048224 -20.471403  78.269010 -20.978442  77.105158   
4         1    6  75.902095 -24.338152  77.113394 -25.133782  76.041404   
...     ...  ...        ...        ...        ...        ...        ...   
21898   233  242  80.008794  44.207091  80.154264  51.282248  78.799314   
21899   233  243  80.760793  36.728885  81.052819  44.273388  79.584925   
21900   233  244  81.338812  28.123821  81.798007  35.890003  80.221703   
21901   233  245  81.705630  18.551148  82.326232  26.541583  80.663323   
21902   233  248  81.338539 -11.314870  82.422114  -7.241076  80.742826   

          lon_UR     lat_LL     lon_LL     lat_LR     lon_LR  
0       2.594563  80.144957 -11.291900  78.789287  -5.405237  
1      -4.156684  79.130143 -17.075937  77.882976 -11.061501  
2     -10.018548  78.034189 -21.909139  76.886141 -15.950291  
3     -14.988030  76.879455 -25.870470  75.819367 -20.086304  
4     -19.307509  75.661913 -29.246411  74.680825 -23.697966  
...          ...        ...        ...        ...        ...  
21898  45.389529  81.215211  42.713538  79.726284  37.379350  
21899  38.823265  81.923478  34.042857  80.327864  29.693888  
21900  31.325044  82.424145  24.005498  80.744047  21.177876  
21901  23.323882  82.678136  12.476933  80.951763  11.702585  
21902  -4.410664  81.795931 -19.109458  80.218989 -14.542426  

[21903 rows x 12 columns]

It also includes the Intake catalog (more on that later), and a spatial index data structure to query the catalog. A query on the object returns a subset of the path/row combinations that bound the query point:

In [5]:
idxs = ls8.query_pathrow(69, -50)   # lat, lon
idxs.data

path  row    lat_CTR    lon_CTR     lat_UL     lon_UL     lat_UR  \
695      8   11  69.606470 -47.813174  70.756261 -49.045943  69.997303   
696      8   12  68.279699 -49.506130  69.419648 -50.743468  68.700888   
782      9   11  69.606482 -49.355231  70.757156 -50.589565  69.997520   
783      9   12  68.279697 -51.046291  69.420484 -52.285488  68.700913   
866     10   11  69.606439 -50.895321  70.756467 -52.132700  69.996319   
6845    81  233  69.606467 -48.202833  69.158069 -44.965508  68.442808   
6915    82  233  69.606440 -49.749759  69.160805 -46.513479  68.444886   
7017    83  232  68.279726 -49.604053  67.806027 -46.581815  67.125546   
7018    83  233  69.606447 -51.293647  69.158697 -48.052981  68.442311   
7087    84  232  68.279691 -51.145138  67.808695 -48.124313  67.127863   

         lon_UR     lat_LL     lon_LL     lat_LR     lon_LR  
695  -44.451408  69.154025 -51.050718  68.439813 -46.725544  
696  -46.367352  67.801954 -52.529493  67.122236 -48.403704  
782  -45.990513  69.153716 -52.595528  68.438861 -48.266305  
783  -47.904523  67.801817 -54.072478  67.121321 -49.942257  
866  -47.530333  69.154836 -54.136166  68.439445 -49.803544  
6845 -49.295142  70.763699 -46.977141  70.002875 -51.580448  
6915 -50.847126  70.761497 -48.518743  70.000130 -53.125468  
7017 -50.709373  69.426907 -48.374276  68.706648 -52.756036  
7018 -52.389424  70.764101 -50.064050  70.002091 -54.674559  
7087 -52.255251  69.424457 -49.910379  68.703970 -54.294948

In [6]:
cpanel = GeoStacksUI(spatial_index=ls8)
cpanel.gen_ui()

AppLayout(children=(VBox(children=(HTML(value='<h2>Drag the marker to your region of interest</h2>'), Select(d…

In [7]:
scene_list = ls8.search_s3(idxs.data.index.to_list())
#scene_list = ls8.search_s3(cpanel.pr_selection)
scene_list

path row  \
acq_time                       
2013-03-19 00:00:00    8  12   
2013-03-27 00:00:00   10  11   
2013-04-01 00:00:00    9  11   
2013-04-11 00:00:00    9  11   
2013-04-18 00:00:00   10  11   
...                  ...  ..   
2021-04-26 00:01:00    8  12   
2021-05-03 00:00:00    9  12   
2021-05-03 00:01:00    9  12   
2021-05-10 00:01:00   10  11   
2021-05-12 00:01:00    8  12   

                                                                prefix  \
acq_time                                                                 
2013-03-19 00:00:00  c1/L8/008/012/LC08_L1TP_008012_20130319_201705...   
2013-03-27 00:00:00  c1/L8/010/011/LC08_L1TP_010011_20130327_201705...   
2013-04-01 00:00:00  c1/L8/009/011/LC08_L1TP_009011_20130401_201705...   
2013-04-11 00:00:00  c1/L8/009/011/LC08_L1TP_009011_20130411_201705...   
2013-04-18 00:00:00  c1/L8/010/011/LC08_L1TP_010011_20130418_201705...   
...                                                                ...   
2021-04-26 00:01:00  c1/L8/008/012/LC08_L1TP_008012_20210426_202104...   
2021-05-03 00:00:00  c1/L8/009/012/LC08_L1TP_009012_20210503_202105...   
2021-05-03 00:01:00  c1/L8/009/012/LC08_L1TP_009012_20210503_202105...   
2021-05-10 00:01:00  c1/L8/010/011/LC08_L1TP_010011_20210510_202105...   
2021-05-12 00:01:00  c1/L8/008/012/LC08_L1TP_008012_20210512_202105...   

                      prc_time tier  
acq_time                             
2013-03-19 00:00:00 2017-05-05   T1  
2013-03-27 00:00:00 2017-05-05   T1  
2013-04-01 00:00:00 2017-05-05   T1  
2013-04-11 00:00:00 2017-05-05   T1  
2013-04-18 00:00:00 2017-05-05   T1  
...                        ...  ...  
2021-04-26 00:01:00 2021-04-26   RT  
2021-05-03 00:00:00 2021-05-08   T1  
2021-05-03 00:01:00 2021-05-03   RT  
2021-05-10 00:01:00 2021-05-10   RT  
2021-05-12 00:01:00 2021-05-12   RT  

[559 rows x 5 columns]

In [8]:
# Closest time
dt = datetime(2016, 3, 1)
close_time = scene_list.index.get_loc(dt, method='nearest')
scene_list.iloc[close_time]

path                                                        9
row                                                        12
prefix      c1/L8/009/012/LC08_L1TP_009012_20160302_201703...
prc_time                                  2017-03-28 00:00:00
tier                                                       T1
Name: 2016-03-02 00:00:00, dtype: object

In [9]:
scene_list[datetime(2016, 2, 12):datetime(2016, 3, 15)]

path row                                             prefix  \
acq_time                                                                 
2016-03-02    9  12  c1/L8/009/012/LC08_L1TP_009012_20160302_201703...   
2016-03-09   10  11  c1/L8/010/011/LC08_L1TP_010011_20160309_201801...   
2016-03-11    8  12  c1/L8/008/012/LC08_L1TP_008012_20160311_201703...   

             prc_time tier  
acq_time                    
2016-03-02 2017-03-28   T1  
2016-03-09 2018-01-30   T1  
2016-03-11 2017-03-28   T1

In [10]:
client = Client(processes=True, n_workers=4, 
                threads_per_worker=1,
                silence_logs=logging.ERROR)
client

<Client: 'tcp://127.0.0.1:43075' processes=4 threads=4, memory=16.55 GB>

In [11]:
# high res pan
idxs.intake.landsat8(path='009',row='012',band_id='B8',
                     base='LC08_L1TP_009012_20160302_20170328_01_T1').to_dask()

<xarray.DataArray (band: 1, y: 17141, x: 17061)>
dask.array<open_rasterio-34cb5fbf48fdc7c3b3ec6cd9cdbd4646<this-array>, shape=(1, 17141, 17061), dtype=uint16, chunksize=(1, 512, 512), chunktype=numpy.ndarray>
Coordinates:
  * band     (band) int64 1
  * y        (y) float64 7.702e+06 7.702e+06 7.702e+06 ... 7.445e+06 7.445e+06
  * x        (x) float64 3.687e+05 3.687e+05 3.687e+05 ... 6.246e+05 6.246e+05
Attributes:
    transform:      (15.0, 0.0, 368692.5, 0.0, -15.0, 7702207.5)
    crs:            +init=epsg:32622
    res:            (15.0, 15.0)
    is_tiled:       1
    nodatavals:     (nan,)
    scales:         (1.0,)
    offsets:        (0.0,)
    AREA_OR_POINT:  Point

In [12]:
# helper functions
def JD(year,month,day):
    "converts to day of year"
    t = time.mktime((year,month,day,0,0,0,0,0,0))
    return int(time.gmtime(t)[7])

def pad(number, length):
    "takes number, cast to string with padded zeros"
    while len(str(number)) < length:
        number = '0' + str(number)
        pad(number, length)
    return number


In [13]:
scene_list_2015 = scene_list[datetime(2015, 1, 1):datetime(2016, 1, 1)]
row = scene_list_2015['row'] == 12
path = scene_list_2015['path'] == 9
tier = scene_list_2015['tier'] == 'T1'
sub = scene_list_2015.where(row & path & tier).dropna()
sub

path row                                             prefix  \
acq_time                                                                 
2015-02-28    9  12  c1/L8/009/012/LC08_L1TP_009012_20150228_201704...   
2015-03-16    9  12  c1/L8/009/012/LC08_L1TP_009012_20150316_201704...   
2015-06-04    9  12  c1/L8/009/012/LC08_L1TP_009012_20150604_201704...   
2015-07-06    9  12  c1/L8/009/012/LC08_L1TP_009012_20150706_201704...   
2015-07-22    9  12  c1/L8/009/012/LC08_L1TP_009012_20150722_201704...   

             prc_time tier  
acq_time                    
2015-02-28 2017-04-12   T1  
2015-03-16 2017-04-12   T1  
2015-06-04 2017-04-08   T1  
2015-07-06 2017-04-07   T1  
2015-07-22 2017-04-06   T1

In [14]:
# Don't know how to suppress warnings =/

daskDoesntSupportIterators = []
for row in sub.itertuples():
    daskDoesntSupportIterators.append(row)

# Function for cleaning the data: rename band -> time and create datetime object
def preprocess(ds, value):
    ds["band"] = [value.to_numpy()]
    ds = ds.rename({'band': 'time'})
    return ds


def retrieve_dataset(row):
    try:
        ds = ls8.intake.landsat8(base=row.prefix[14:-1],
                                 path=pad(row.path, 3),
                                 row=pad(row.row, 3),
                                 band_id='BQA').to_dask()
        return preprocess(ds, row.Index)
    except Exception:
        return None


datasets = client.map(retrieve_dataset, daskDoesntSupportIterators)
datasets = client.gather(datasets)
datasets = [dataset for dataset in datasets if dataset is not None]
ds = xr.concat(datasets, dim='time', compat='override', coords='minimal').squeeze()
ds

/nix/store/jnb7546595v814aybav2r6p5sxyz68d7-python3-3.8.9-env/lib/python3.8/site-packages/dask/array/core.py:4292: PerformanceWarning: Increasing number of chunks by factor of 17
  result = blockwise(
/nix/store/jnb7546595v814aybav2r6p5sxyz68d7-python3-3.8.9-env/lib/python3.8/site-packages/dask/array/core.py:4292: PerformanceWarning: Increasing number of chunks by factor of 17
  result = blockwise(
/nix/store/jnb7546595v814aybav2r6p5sxyz68d7-python3-3.8.9-env/lib/python3.8/site-packages/dask/array/core.py:4292: PerformanceWarning: Increasing number of chunks by factor of 17
  result = blockwise(
/nix/store/jnb7546595v814aybav2r6p5sxyz68d7-python3-3.8.9-env/lib/python3.8/site-packages/dask/array/core.py:4292: PerformanceWarning: Increasing number of chunks by factor of 17
  result = blockwise(
/nix/store/jnb7546595v814aybav2r6p5sxyz68d7-python3-3.8.9-env/lib/python3.8/site-packages/dask/array/core.py:4292: PerformanceWarning: Increasing number of chunks by factor of 17
  result = blockw

<xarray.DataArray (time: 5, y: 8581, x: 8671)>
dask.array<concatenate, shape=(5, 8581, 8671), dtype=float64, chunksize=(1, 512, 512), chunktype=numpy.ndarray>
Coordinates:
  * x        (x) float64 3.678e+05 3.678e+05 3.679e+05 ... 6.279e+05 6.279e+05
  * y        (y) float64 7.445e+06 7.445e+06 7.445e+06 ... 7.702e+06 7.702e+06
  * time     (time) datetime64[ns] 2015-02-28 2015-03-16 ... 2015-07-22
Attributes:
    transform:      (30.0, 0.0, 367785.0, 0.0, -30.0, 7702215.0)
    crs:            +init=epsg:32622
    res:            (30.0, 30.0)
    is_tiled:       1
    nodatavals:     (nan,)
    scales:         (1.0,)
    offsets:        (0.0,)
    AREA_OR_POINT:  Point

In [15]:
import hvplot.xarray

width = 800
height = 400
widget_type = 'scrubber'
widget_location = 'bottom'


ds.hvplot.image(
    rasterize=True,
    aspect='equal',
    x="x",
    y="y",
    cmap='gray',
    clim=(2732, 2813),
    width=width,
    height=height,
    widget_type=widget_type,
    widget_location=widget_location,
)

Column
    [0] HoloViews(DynamicMap, widget_location='bottom', widget_type='scrubber')
    [1] Row
        [0] HSpacer()
        [1] WidgetBox
            [0] Player(end=4, width=550)
        [2] HSpacer()